## X-ray image loading and analysis

In [1]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import os, cv2, json, shutil
import tensorflow as tf
import seaborn as sns


from sklearn.model_selection import train_test_split
from sklearn.metrics import confusion_matrix

from tensorflow.keras.applications import VGG16
from tensorflow.keras.layers import Input
from keras.preprocessing import image_dataset_from_directory
from keras.preprocessing.image import ImageDataGenerator, array_to_img, img_to_array, load_img
from keras import models, layers, regularizers
from keras.callbacks import EarlyStopping, ModelCheckpoint

In [2]:
metadata = pd.read_csv('COVID19_SBU/metadata.csv')

metadata.head(5)

id patient_id  enhanced                          series  \
0  IMG00001    A000801     False  01-03-1901-CHEST AP PORT-62879   
1  IMG00002    A000801      True  01-03-1901-CHEST AP PORT-62879   
2  IMG00003    A000801     False  01-03-1901-CHEST AP PORT-62879   
3  IMG00004    A000801      True  01-03-1901-CHEST AP PORT-62879   
4  IMG00005    A000801     False  01-04-1901-CHEST AP PORT-17928   

                                            filename  
0  A000801/01-03-1901-CHEST AP PORT-62879/1.00000...  
1  A000801/01-03-1901-CHEST AP PORT-62879/2.00000...  
2  A000801/01-03-1901-CHEST AP PORT-62879/3.00000...  
3  A000801/01-03-1901-CHEST AP PORT-62879/4.00000...  
4  A000801/01-04-1901-CHEST AP PORT-17928/1.00000...

In [3]:
metadata['filename'][0]

'A000801/01-03-1901-CHEST AP PORT-62879/1.000000-AP-12195/1-1.png'

In [4]:
metadata['enhanced'].value_counts()

False    6938
True     6700
Name: enhanced, dtype: int64

In [5]:
metadata.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 13638 entries, 0 to 13637
Data columns (total 5 columns):
 #   Column      Non-Null Count  Dtype 
---  ------      --------------  ----- 
 0   id          13638 non-null  object
 1   patient_id  13638 non-null  object
 2   enhanced    13638 non-null  bool  
 3   series      13638 non-null  object
 4   filename    13638 non-null  object
dtypes: bool(1), object(4)
memory usage: 439.6+ KB


In [6]:
metadata.columns

Index(['id', 'patient_id', 'enhanced', 'series', 'filename'], dtype='object')

In [7]:
metadata.patient_id.value_counts()

A860070    236
A763364    183
A221230    175
A701295    174
A766483    173
          ... 
A337940      1
A940723      1
A685471      1
A434920      1
A647750      1
Name: patient_id, Length: 1365, dtype: int64

In [8]:
len(metadata.patient_id.unique())

1365

In [9]:
#only keep enhanced images
metadata.drop(metadata[metadata['enhanced'] == False].index, inplace=True)
metadata.head()

id patient_id  enhanced                          series  \
1  IMG00002    A000801      True  01-03-1901-CHEST AP PORT-62879   
3  IMG00004    A000801      True  01-03-1901-CHEST AP PORT-62879   
5  IMG00006    A000801      True  01-04-1901-CHEST AP PORT-17928   
7  IMG00008    A000801      True  01-04-1901-CHEST AP PORT-17928   
9  IMG00010    A000801      True  01-04-1901-CHEST AP PORT-38592   

                                            filename  
1  A000801/01-03-1901-CHEST AP PORT-62879/2.00000...  
3  A000801/01-03-1901-CHEST AP PORT-62879/4.00000...  
5  A000801/01-04-1901-CHEST AP PORT-17928/2.00000...  
7  A000801/01-04-1901-CHEST AP PORT-17928/4.00000...  
9  A000801/01-04-1901-CHEST AP PORT-38592/2.00000...

In [10]:
metadata.filename[1]

'A000801/01-03-1901-CHEST AP PORT-62879/2.000000-AP-20460/1-1.png'

In [11]:
df = pd.read_csv('df.csv')
df.head()

patient_id last.status  is_icu  length_of_stay  days_prior_sx  \
0    A917122  discharged     0.0             9.0           10.6   
1    A387558    deceased     1.0            15.0            4.2   
2    A968238    deceased     1.0            28.0            4.0   
3    A106133    deceased     0.0             4.0            6.0   
4    A300871    deceased     0.0             3.0            6.0   

   8331-1_Oral temperature  \
0                     36.4   
1                     37.0   
2                     37.4   
3                     36.7   
4                     36.7   

   59408-5_Oxygen saturation in Arterial blood by Pulse oximetry  \
0                                               91.0               
1                                              100.0               
2                                               84.0               
3                                               96.0               
4                                               97.0               

   9279-1_Respiratory rate  76282-3_Heart rate.beat-to-beat by EKG  \
0                     22.0                                    86.0   
1                     39.0                                   149.0   
2                     42.0                                    88.0   
3                     16.0                                   100.0   
4                     20.0                                    94.0   

   8480-6_Systolic blood pressure  ...  x7_False  x7_True  x8_False  x8_True  \
0                           172.0  ...       1.0      0.0       1.0      0.0   
1                           158.0  ...       0.0      1.0       0.0      1.0   
2                           130.0  ...       0.0      1.0       1.0      0.0   
3                           132.0  ...       1.0      0.0       1.0      0.0   
4                           104.0  ...       1.0      0.0       1.0      0.0   

   x9_False  x9_True  x10_False  x10_True  x11_False  x11_True  
0       1.0      0.0        1.0       0.0        0.0       1.0  
1       1.0      0.0        1.0       0.0        0.0       1.0  
2       1.0      0.0        0.0       1.0        1.0       0.0  
3       1.0      0.0        0.0       1.0        1.0       0.0  
4       0.0      1.0        1.0       0.0        1.0       0.0  

[5 rows x 58 columns]

In [12]:
deceased = list(df[df['last.status'] == 'deceased']['patient_id'].values)

In [13]:
deceased[1]

'A968238'

In [14]:
discharged = list(df[df['last.status'] == 'discharged']['patient_id'].values)

In [15]:
discharged[1]

'A205701'

In [16]:
len(metadata['patient_id'].unique())

1332

In [17]:
len(df['patient_id'].unique())

1313

In [18]:
#patient ids for deceased
deceased_list = []
for val in metadata['patient_id'].unique():
    if val in deceased:
        deceased_list.append(val)
        
print(deceased_list)

['A003797', 'A022063', 'A025840', 'A035738', 'A036454', 'A045719', 'A045825', 'A046441', 'A093640', 'A099036', 'A111996', 'A113828', 'A116097', 'A121362', 'A134763', 'A149204', 'A151238', 'A157535', 'A160394', 'A172636', 'A178769', 'A188884', 'A193060', 'A198573', 'A203151', 'A207634', 'A223205', 'A235514', 'A237035', 'A240623', 'A243413', 'A256889', 'A274721', 'A279745', 'A292777', 'A294515', 'A294890', 'A296549', 'A300871', 'A322143', 'A327062', 'A329601', 'A340955', 'A348739', 'A349708', 'A353550', 'A363883', 'A370011', 'A372249', 'A373370', 'A373660', 'A376320', 'A379944', 'A387558', 'A389295', 'A390622', 'A390754', 'A390915', 'A438102', 'A451097', 'A458393', 'A460744', 'A487800', 'A492240', 'A512163', 'A523411', 'A533789', 'A547200', 'A549020', 'A555392', 'A563909', 'A574117', 'A590713', 'A602816', 'A607170', 'A609649', 'A616705', 'A619446', 'A625730', 'A642300', 'A649144', 'A652157', 'A652563', 'A656088', 'A665943', 'A672510', 'A683471', 'A700420', 'A703838', 'A704496', 'A724189'

In [19]:
#patient ids for discharged

discharged_list = []
for v in metadata['patient_id'].unique():
    if v in discharged:
        discharged_list.append(v)
        
print(discharged_list)

['A000801', 'A000936', 'A001375', 'A001942', 'A002052', 'A002279', 'A002304', 'A002471', 'A005097', 'A005163', 'A008984', 'A010092', 'A012155', 'A013939', 'A014950', 'A016973', 'A017004', 'A017227', 'A018604', 'A019571', 'A019709', 'A020215', 'A020333', 'A020519', 'A021084', 'A023023', 'A023095', 'A023545', 'A027284', 'A027914', 'A028914', 'A030428', 'A030820', 'A032808', 'A033072', 'A033798', 'A034518', 'A035785', 'A038399', 'A038686', 'A038694', 'A040293', 'A041535', 'A041791', 'A042028', 'A042105', 'A042359', 'A042732', 'A048184', 'A048221', 'A048383', 'A049756', 'A050656', 'A051249', 'A051275', 'A051538', 'A051693', 'A055532', 'A056213', 'A056396', 'A056642', 'A057551', 'A057590', 'A058062', 'A059254', 'A059961', 'A060176', 'A062055', 'A062143', 'A062576', 'A064463', 'A064803', 'A066131', 'A067967', 'A068387', 'A069414', 'A071079', 'A071186', 'A071499', 'A071731', 'A071880', 'A072894', 'A073761', 'A074083', 'A075466', 'A077598', 'A077796', 'A077831', 'A079927', 'A079945', 'A080214'

In [20]:
metadata.loc[metadata['patient_id'] == 'A022063', 'filename']

371    A022063/01-08-1901-CHEST AP PORT-43082/2.00000...
373    A022063/12-31-1900-CHEST AP VIEW ONLY-85175/2....
Name: filename, dtype: object

In [21]:
for val in deceased_list:
    for x in metadata['patient_id']:
        if val == x:
            print(metadata.loc[metadata['patient_id'] == val, 'filename'])

211    A003797/01-01-1901-CHEST AP PORT-61015/4.00000...
213    A003797/01-02-1901-CHEST AP PORT CENTRAL LINE ...
215    A003797/01-02-1901-CHEST AP PORT-85497/4.00000...
217    A003797/01-03-1901-CHEST AP PORT-44037/2.00000...
219    A003797/01-04-1901-CHEST AP PORT-13951/2.00000...
221    A003797/01-05-1901-CHEST AP PORT-29050/4.00000...
223    A003797/01-06-1901-CHEST AP PORT-31683/5.00000...
225    A003797/01-07-1901-CHEST AP PORT-32945/2.00000...
227    A003797/01-08-1901-CHEST AP PORT-51626/2.00000...
229    A003797/01-09-1901-CHEST AP PORT-58101/2.00000...
231    A003797/01-10-1901-CHEST AP PORT-41137/2.00000...
233    A003797/01-10-1901-CHEST AP PORT-58200/2.00000...
235    A003797/01-10-1901-CHEST AP PORT-58200/4.00000...
237    A003797/01-11-1901-CHEST AP PORT-37757/2.00000...
239    A003797/01-12-1901-CHEST AP PORT-79384/2.00000...
241    A003797/01-13-1901-CHEST AP PORT-01766/2.00000...
243    A003797/01-13-1901-CHEST AP PORT-30308/5.00000...
245    A003797/01-14-1901-CHEST

Name: filename, dtype: object
1608    A134763/01-01-1901-CHEST AP PORT-30237/2.00000...
1610    A134763/01-02-1901-CHEST AP PORT-39789/2.00000...
1612    A134763/01-03-1901-CHEST AP PORT-60532/2.00000...
1614    A134763/01-03-1901-CHEST AP VIEWONLY-09188/3.0...
1616    A134763/01-03-1901-CHEST AP VIEWONLY-09188/4.0...
1618    A134763/01-04-1901-CHEST AP PORT-13259/2.00000...
1620    A134763/01-04-1901-CHEST AP PORT-92484/4.00000...
1622    A134763/01-05-1901-CHEST AP PORT-84062/2.00000...
1624    A134763/01-06-1901-CHEST AP PORT-82948/2.00000...
1626    A134763/01-06-1901-CHEST AP PORT-82948/4.00000...
1628    A134763/01-07-1901-CHEST AP PORT-30584/2.00000...
1630    A134763/01-07-1901-CHEST AP PORT-44227/2.00000...
1632    A134763/01-07-1901-CHEST AP PORT-44227/6.00000...
1634    A134763/01-07-1901-CHEST AP PORT-93887/2.00000...
1636    A134763/01-08-1901-CHEST AP PORT-27026/3.00000...
1638    A134763/01-09-1901-CHEST AP PORT-86407/2.00000...
1640    A134763/01-10-1901-CHEST AP PORT-3

Name: filename, dtype: object
2960    A256889/01-02-1901-CHEST AP PORT-73559/2.00000...
2962    A256889/01-05-1901-CHEST AP VIEWONLY-94471/2.0...
2964    A256889/01-13-1901-CHEST AP PORT CENTRAL LINE ...
2966    A256889/01-13-1901-CHEST AP PORT CENTRAL LINE ...
2968    A256889/01-16-1901-CHEST AP PORT-13544/2.00000...
2971    A256889/01-17-1901-CHEST AP PORT-59805/5.00000...
2972    A256889/01-17-1901-CHEST AP PORT-59805/6.00000...
2974    A256889/01-18-1901-CHEST AP PORT-92659/2.00000...
2976    A256889/01-19-1901-CHEST AP PORT-80026/2.00000...
2978    A256889/01-19-1901-CHEST AP PORT-91368/2.00000...
2980    A256889/01-20-1901-CHEST AP PORT-30893/2.00000...
2982    A256889/01-21-1901-CHEST AP PORT-96601/2.00000...
2984    A256889/01-22-1901-CHEST AP PORT-59993/4.00000...
2986    A256889/01-23-1901-CHEST AP PORT-34819/3.00000...
2988    A256889/01-24-1901-CHEST AP PORT-01830/5.00000...
2991    A256889/01-24-1901-CHEST AP PORT-37202/5.00000...
2992    A256889/01-24-1901-CHEST AP PORT-3

Name: filename, dtype: object
3849    A349708/01-01-1901-CHEST AP PORT-08184/2.00000...
3851    A349708/01-04-1901-CHEST AP PORT-26373/2.00000...
3853    A349708/01-04-1901-CHEST AP PORT-80668/5.00000...
3855    A349708/01-05-1901-CHEST AP PORT-42707/2.00000...
3857    A349708/01-07-1901-CHEST AP PORT-22302/5.00000...
3860    A349708/01-10-1901-CHEST AP PORT-35964/4.00000...
3861    A349708/01-10-1901-CHEST AP PORT-35964/5.00000...
3863    A349708/01-14-1901-CHEST AP PORT-58556/5.00000...
3865    A349708/01-15-1901-CHEST AP PORT-04194/3.00000...
3868    A349708/01-16-1901-CHEST AP PORT-68132/3.00000...
3869    A349708/01-16-1901-CHEST AP PORT-68132/4.00000...
3871    A349708/01-17-1901-CHEST AP PORT-01684/5.00000...
3873    A349708/01-18-1901-CHEST AP PORT-55838/2.00000...
3875    A349708/01-18-1901-CHEST AP PORT-89033/4.00000...
3877    A349708/01-19-1901-CHEST AP PORT-98796/2.00000...
3879    A349708/01-20-1901-CHEST AP PORT-10021/4.00000...
3881    A349708/01-20-1901-CHEST AP PORT-8

4475    A372249/01-19-1901-CHEST AP VIEWONLY-46238/4.0...
4479    A372249/12-24-1900-CHEST AP VIEWONLY-53704/2.0...
4481    A372249/12-25-1900-CHEST AP PORT CENTRAL LINE ...
4483    A372249/12-25-1900-CHEST AP PORT-36513/2.00000...
4485    A372249/12-25-1900-CHEST AP PORT-82648/2.00000...
4487    A372249/12-26-1900-CHEST AP PORT-27928/2.00000...
4489    A372249/12-27-1900-CHEST AP PORT-76135/2.00000...
4491    A372249/12-28-1900-CHEST AP PORT-69875/2.00000...
4493    A372249/12-29-1900-CHEST AP PORT-32600/4.00000...
4495    A372249/12-30-1900-CHEST AP PORT-34654/2.00000...
4497    A372249/12-31-1900-CHEST AP VIEWONLY-02383/2.0...
Name: filename, dtype: object
4475    A372249/01-19-1901-CHEST AP VIEWONLY-46238/4.0...
4479    A372249/12-24-1900-CHEST AP VIEWONLY-53704/2.0...
4481    A372249/12-25-1900-CHEST AP PORT CENTRAL LINE ...
4483    A372249/12-25-1900-CHEST AP PORT-36513/2.00000...
4485    A372249/12-25-1900-CHEST AP PORT-82648/2.00000...
4487    A372249/12-26-1900-CHEST AP PORT-2

...

7722    A652157/01-06-1901-CHEST AP VIEWONLY-78884/2.0...
7724    A652157/01-11-1901-CHEST AP PORT-40970/2.00000...
7726    A652157/01-12-1901-CHEST AP VIEWONLY-05895/3.0...
7728    A652157/01-14-1901-CHEST AP PORT-23007/5.00000...
7730    A652157/01-20-1901-CHEST AP PORT-91861/5.00000...
7732    A652157/01-21-1901-CHEST AP PORT-83100/5.00000...
7734    A652157/01-21-1901-CHEST AP PORT-94223/5.00000...
7736    A652157/01-22-1901-CHEST AP PORT-58283/5.00000...
7738    A652157/12-29-1900-CHEST AP VIEWONLY-88229/2.0...
7740    A652157/12-31-1900-CHEST AP PORT-83633/2.00000...
Name: filename, dtype: object
7722    A652157/01-06-1901-CHEST AP VIEWONLY-78884/2.0...
7724    A652157/01-11-1901-CHEST AP PORT-40970/2.00000...
7726    A652157/01-12-1901-CHEST AP VIEWONLY-05895/3.0...
7728    A652157/01-14-1901-CHEST AP PORT-23007/5.00000...
7730    A652157/01-20-1901-CHEST AP PORT-91861/5.00000...
7732    A652157/01-21-1901-CHEST AP PORT-83100/5.00000...
7734    A652157/01-21-1901-CHEST AP PORT-9

8703    A727037/01-01-1901-CHEST AP PORT-38989/2.00000...
8705    A727037/01-03-1901-CHEST AP PORT-94191/2.00000...
8707    A727037/01-03-1901-CHEST AP PORT-94191/4.00000...
8709    A727037/01-04-1901-CHEST AP VIEWONLY-31060/2.0...
8711    A727037/01-05-1901-CHEST AP VIEWONLY-34562/2.0...
                              ...                        
8841    A727037/12-10-1900-CHEST AP VIEWONLY-52958/2.0...
8842    A727037/12-10-1900-CHEST AP VIEWONLY-52958/3.0...
8845    A727037/12-11-1900-CHEST AP PORT-62557/4.00000...
8847    A727037/12-25-1900-CHEST AP VIEWONLY-81309/2.0...
8849    A727037/12-31-1900-CHEST AP PORT-82828/4.00000...
Name: filename, Length: 73, dtype: object
8703    A727037/01-01-1901-CHEST AP PORT-38989/2.00000...
8705    A727037/01-03-1901-CHEST AP PORT-94191/2.00000...
8707    A727037/01-03-1901-CHEST AP PORT-94191/4.00000...
8709    A727037/01-04-1901-CHEST AP VIEWONLY-31060/2.0...
8711    A727037/01-05-1901-CHEST AP VIEWONLY-34562/2.0...
                              

Name: filename, dtype: object
9789    A769593/01-06-1901-CHEST AP PORT-76497/2.00000...
9791    A769593/01-07-1901-CHEST AP PORT-16141/2.00000...
9793    A769593/01-07-1901-CHEST AP PORT-81916/2.00000...
9795    A769593/01-08-1901-CHEST AP PORT-16326/2.00000...
9797    A769593/01-08-1901-CHEST AP PORT-35258/2.00000...
9799    A769593/01-08-1901-CHEST AP VIEWONLY-19004/2.0...
9801    A769593/01-09-1901-CHEST AP VIEWONLY-16065/2.0...
9803    A769593/01-09-1901-CHEST AP VIEWONLY-16065/4.0...
9805    A769593/01-10-1901-CHEST AP PORT-88615/2.00000...
9807    A769593/01-11-1901-CHEST AP PORT-18734/5.00000...
9809    A769593/01-11-1901-CHEST AP PORT-88338/3.00000...
9811    A769593/01-12-1901-CHEST AP PORT-05327/5.00000...
9813    A769593/01-12-1901-CHEST AP PORT-41910/5.00000...
9815    A769593/01-12-1901-CHEST AP PORT-71408/3.00000...
9817    A769593/01-12-1901-CHEST AP PORT-95034/5.00000...
9819    A769593/01-12-1901-CHEST AP VIEWONLY-54843/5.0...
9821    A769593/01-13-1901-CHEST AP PORT-7

Name: filename, dtype: object
10360    A808584/01-03-1901-CHEST AP PORT-59987/2.00000...
10362    A808584/01-05-1901-CHEST AP PORT-01343/2.00000...
10364    A808584/01-07-1901-CHEST AP PORT-05118/2.00000...
10366    A808584/01-09-1901-CHEST AP PORT-34535/2.00000...
10368    A808584/01-09-1901-CHEST AP PORT-96338/2.00000...
10370    A808584/01-11-1901-CHEST AP PORT-69804/2.00000...
10372    A808584/01-12-1901-CHEST AP PORT-47355/3.00000...
10374    A808584/01-13-1901-CHEST AP PORT-24391/4.00000...
10376    A808584/01-14-1901-CHEST AP PORT-91472/5.00000...
10379    A808584/01-15-1901-CHEST AP PORT-84474/5.00000...
10380    A808584/01-15-1901-CHEST AP PORT-84474/6.00000...
10382    A808584/01-16-1901-CHEST AP PORT-73105/3.00000...
10384    A808584/01-16-1901-CHEST AP PORT-90370/5.00000...
10386    A808584/01-17-1901-CHEST AP PORT-67613/2.00000...
10388    A808584/01-19-1901-CHEST AP PORT-30950/5.00000...
10390    A808584/01-20-1901-CHEST AP PORT-77737/5.00000...
10392    A808584/01-21-190

Name: filename, dtype: object
11738    A866354/01-01-1901-CHEST AP PORT-79482/2.00000...
11740    A866354/01-08-1901-CHEST AP VIEWONLY-88566/2.0...
11742    A866354/01-09-1901-CHEST AP PORT CENTRAL LINE ...
11744    A866354/01-09-1901-CHEST AP PORT-39717/2.00000...
11747    A866354/01-16-1901-CHEST AP VIEWONLY-49798/3.0...
11749    A866354/01-22-1901-CHEST AP PORT-80274/2.00000...
11751    A866354/12-30-1900-CHEST AP VIEWONLY-21494/2.0...
11753    A866354/12-31-1900-CHEST AP PORT-43001/4.00000...
11755    A866354/12-31-1900-CHEST AP PORT-54150/4.00000...
11757    A866354/12-31-1900-CHEST AP VIEWONLY-62467/2.0...
Name: filename, dtype: object
11738    A866354/01-01-1901-CHEST AP PORT-79482/2.00000...
11740    A866354/01-08-1901-CHEST AP VIEWONLY-88566/2.0...
11742    A866354/01-09-1901-CHEST AP PORT CENTRAL LINE ...
11744    A866354/01-09-1901-CHEST AP PORT-39717/2.00000...
11747    A866354/01-16-1901-CHEST AP VIEWONLY-49798/3.0...
11749    A866354/01-22-1901-CHEST AP PORT-80274/2.00000

In [22]:
for val in discharged_list:
    for x in metadata['patient_id']:
        if val == x:
            print(metadata.loc[metadata['patient_id'] == val, 'filename'])

1     A000801/01-03-1901-CHEST AP PORT-62879/2.00000...
3     A000801/01-03-1901-CHEST AP PORT-62879/4.00000...
5     A000801/01-04-1901-CHEST AP PORT-17928/2.00000...
7     A000801/01-04-1901-CHEST AP PORT-17928/4.00000...
9     A000801/01-04-1901-CHEST AP PORT-38592/2.00000...
11    A000801/01-04-1901-CHEST AP VIEWONLY-33193/2.0...
13    A000801/01-06-1901-CHEST AP VIEWONLY-38510/2.0...
15    A000801/01-07-1901-CHEST AP VIEWONLY-24318/2.0...
17    A000801/01-08-1901-CHEST AP PORT-96486/2.00000...
19    A000801/01-09-1901-CHEST AP PORT-30406/2.00000...
21    A000801/01-10-1901-CHEST AP PORT-72414/2.00000...
23    A000801/01-11-1901-CHEST AP PORT-86305/3.00000...
25    A000801/01-12-1901-CHEST AP PORT-14997/5.00000...
27    A000801/01-14-1901-CHEST AP VIEWONLY-60953/3.0...
29    A000801/01-19-1901-CHEST AP VIEWONLY-31486/5.0...
31    A000801/01-20-1901-CHEST AP PORT-27769/3.00000...
33    A000801/01-23-1901-CHEST AP PORT-09676/5.00000...
35    A000801/02-10-1901-CHEST AP PORT-75231/3.0

355    A019709/01-08-1901-CHEST AP VIEWONLY-83019/2.0...
357    A019709/12-31-1900-CHEST AP PORT-90988/2.00000...
Name: filename, dtype: object
359    A020215/12-22-1900-CHEST AP VIEWONLY-89272/5.0...
361    A020215/12-31-1900-CHEST AP VIEWONLY-70228/2.0...
Name: filename, dtype: object
359    A020215/12-22-1900-CHEST AP VIEWONLY-89272/5.0...
361    A020215/12-31-1900-CHEST AP VIEWONLY-70228/2.0...
Name: filename, dtype: object
363    A020333/12-31-1900-CHEST AP PORT-62004/4.00000...
Name: filename, dtype: object
365    A020519/01-01-1901-CHEST AP VIEWONLY-14930/2.0...
367    A020519/12-31-1900-CHEST AP PORT-94782/2.00000...
Name: filename, dtype: object
365    A020519/01-01-1901-CHEST AP VIEWONLY-14930/2.0...
367    A020519/12-31-1900-CHEST AP PORT-94782/2.00000...
Name: filename, dtype: object
369    A021084/12-31-1900-CHEST AP VIEWONLY-03804/2.0...
Name: filename, dtype: object
375    A023023/12-31-1900-CHEST AP PORT-49737/4.00000...
Name: filename, dtype: object
377    A023095/12-3

613    A059961/12-25-1900-CHEST AP VIEWONLY-75201/2.0...
615    A059961/12-31-1900-CHEST AP PORT-08406/2.00000...
Name: filename, dtype: object
617    A060176/12-31-1900-CHEST AP VIEWONLY-77634/2.0...
Name: filename, dtype: object
619    A062055/12-01-1900-CHEST AP PORT-37428/2.00000...
621    A062055/12-04-1900-CHEST AP PORT-03547/2.00000...
623    A062055/12-06-1900-CHEST AP PORT-72526/2.00000...
625    A062055/12-28-1900-CHEST AP PORT-47386/2.00000...
627    A062055/12-28-1900-CHEST AP PORT-47386/4.00000...
629    A062055/12-31-1900-CHEST AP PORT-97398/2.00000...
Name: filename, dtype: object
619    A062055/12-01-1900-CHEST AP PORT-37428/2.00000...
621    A062055/12-04-1900-CHEST AP PORT-03547/2.00000...
623    A062055/12-06-1900-CHEST AP PORT-72526/2.00000...
625    A062055/12-28-1900-CHEST AP PORT-47386/2.00000...
627    A062055/12-28-1900-CHEST AP PORT-47386/4.00000...
629    A062055/12-31-1900-CHEST AP PORT-97398/2.00000...
Name: filename, dtype: object
619    A062055/12-01-1900

Name: filename, dtype: object
889    A096081/01-01-1901-CHEST AP VIEWONLY-27543/4.0...
891    A096081/01-03-1901-CHEST AP PORT-60695/2.00000...
893    A096081/01-03-1901-CHEST AP PORT-60695/4.00000...
895    A096081/01-04-1901-CHEST AP PORT-69973/2.00000...
897    A096081/01-05-1901-CHEST AP PORT-14169/2.00000...
899    A096081/01-06-1901-CHEST AP PORT-24485/2.00000...
901    A096081/01-07-1901-CHEST AP VIEWONLY-07939/4.0...
903    A096081/01-08-1901-CHEST AP VIEWONLY-17855/2.0...
905    A096081/01-09-1901-CHEST AP VIEWONLY-57542/2.0...
907    A096081/01-10-1901-CHEST AP VIEWONLY-65046/2.0...
909    A096081/01-11-1901-CHEST AP VIEWONLY-81221/2.0...
911    A096081/01-12-1901-CHEST AP PORT-35107/2.00000...
913    A096081/01-13-1901-CHEST AP PORT-19837/2.00000...
915    A096081/01-14-1901-CHEST AP PORT-19179/4.00000...
917    A096081/01-15-1901-CHEST AP PORT-34427/2.00000...
919    A096081/01-15-1901-CHEST AP PORT-34427/4.00000...
921    A096081/01-15-1901-CHEST AP PORT-93136/2.00000...
9

Name: filename, dtype: object
1236    A111874/12-31-1900-CHEST AP VIEWONLY-40146/2.0...
Name: filename, dtype: object
1238    A111952/12-31-1900-CHEST AP PORT-69920/2.00000...
Name: filename, dtype: object
1246    A112293/01-01-1901-CHEST AP VIEWONLY-34228/2.0...
Name: filename, dtype: object
1249    A113004/01-01-1901-CHEST AP PORT CENTRAL LINE ...
1250    A113004/01-01-1901-CHEST AP PORT CENTRAL LINE ...
1252    A113004/01-02-1901-CHEST AP PORT-31322/2.00000...
1254    A113004/01-03-1901-CHEST AP PORT-52179/4.00000...
1256    A113004/01-04-1901-CHEST AP PORT-31839/4.00000...
1258    A113004/01-05-1901-CHEST AP PORT-52470/2.00000...
1260    A113004/01-11-1901-CHEST AP PORT-47446/2.00000...
1262    A113004/01-12-1901-CHEST AP PORT-64339/2.00000...
1265    A113004/12-31-1900-CHEST AP PORT CENTRAL LINE ...
Name: filename, dtype: object
1249    A113004/01-01-1901-CHEST AP PORT CENTRAL LINE ...
1250    A113004/01-01-1901-CHEST AP PORT CENTRAL LINE ...
1252    A113004/01-02-1901-CHEST AP PO

...

Name: filename, dtype: object
12057    A892507/01-02-1901-CHEST AP PORT-75530/3.00000...
12059    A892507/01-03-1901-CHEST AP VIEWONLY-38496/3.0...
12061    A892507/01-04-1901-CHEST AP PORT-33559/2.00000...
12063    A892507/01-05-1901-CHEST AP PORT-73411/3.00000...
12065    A892507/01-06-1901-CHEST AP VIEWONLY-51814/5.0...
12069    A892507/01-07-1901-CHEST AP PORT-46682/3.00000...
12070    A892507/01-07-1901-CHEST AP PORT-46682/4.00000...
12072    A892507/01-07-1901-CHEST AP PORT-88656/3.00000...
12074    A892507/01-08-1901-CHEST AP PORT-65126/3.00000...
12076    A892507/01-09-1901-CHEST AP PORT-77590/4.00000...
12078    A892507/01-10-1901-CHEST AP PORT-66192/2.00000...
12080    A892507/01-11-1901-CHEST AP PORT-60260/3.00000...
12082    A892507/01-12-1901-CHEST AP PORT-43648/3.00000...
12084    A892507/01-13-1901-CHEST AP VIEWONLY-46088/5.0...
12086    A892507/01-14-1901-CHEST AP PORT-32891/5.00000...
12088    A892507/01-15-1901-CHEST AP VIEWONLY-88166/2.0...
12090    A892507/01-16-190

Name: filename, dtype: object
12362    A923527/01-01-1901-CHEST AP PORT-74119/4.00000...
12364    A923527/01-02-1901-CHEST AP PORT-82242/2.00000...
12366    A923527/01-03-1901-CHEST AP PORT-85739/2.00000...
12368    A923527/01-03-1901-CHEST AP PORT-90307/2.00000...
12370    A923527/01-04-1901-CHEST AP PORT-12922/2.00000...
12372    A923527/01-04-1901-CHEST AP VIEWONLY-90538/2.0...
12374    A923527/01-05-1901-CHEST AP PORT-04907/2.00000...
12376    A923527/01-06-1901-CHEST AP PORT-84411/2.00000...
12378    A923527/01-07-1901-CHEST AP PORT-94314/2.00000...
12380    A923527/01-08-1901-CHEST AP PORT-29934/2.00000...
12382    A923527/01-08-1901-CHEST AP VIEWONLY-45389/2.0...
12384    A923527/01-09-1901-CHEST AP VIEWONLY-48959/2.0...
12386    A923527/01-10-1901-CHEST AP PORT-51166/2.00000...
12388    A923527/01-11-1901-CHEST AP PORT-19309/2.00000...
12390    A923527/01-12-1901-CHEST AP PORT-61237/2.00000...
12392    A923527/01-13-1901-CHEST AP PORT-94252/2.00000...
12394    A923527/01-14-190

Name: filename, dtype: object
12662    A943730/01-07-1901-CHEST AP PORT CENTRAL LINE ...
12664    A943730/01-10-1901-CHEST AP VIEWONLY-25519/2.0...
12666    A943730/12-09-1900-CHEST AP VIEWONLY-13290/2.0...
12668    A943730/12-26-1900-CHEST AP VIEWONLY-62996/2.0...
12670    A943730/12-29-1900-CHEST AP PORT-36400/2.00000...
12672    A943730/12-31-1900-CHEST AP PORT-98357/2.00000...
Name: filename, dtype: object
12662    A943730/01-07-1901-CHEST AP PORT CENTRAL LINE ...
12664    A943730/01-10-1901-CHEST AP VIEWONLY-25519/2.0...
12666    A943730/12-09-1900-CHEST AP VIEWONLY-13290/2.0...
12668    A943730/12-26-1900-CHEST AP VIEWONLY-62996/2.0...
12670    A943730/12-29-1900-CHEST AP PORT-36400/2.00000...
12672    A943730/12-31-1900-CHEST AP PORT-98357/2.00000...
Name: filename, dtype: object
12662    A943730/01-07-1901-CHEST AP PORT CENTRAL LINE ...
12664    A943730/01-10-1901-CHEST AP VIEWONLY-25519/2.0...
12666    A943730/12-09-1900-CHEST AP VIEWONLY-13290/2.0...
12668    A943730/12-26-19

13120    A973206/01-01-1901-CHEST AP PORT CENTRAL LINE ...
13122    A973206/01-01-1901-CHEST AP PORT CENTRAL LINE ...
13124    A973206/01-02-1901-CHEST AP PORT-82807/2.00000...
13126    A973206/01-03-1901-CHEST AP PORT-48846/2.00000...
13128    A973206/01-04-1901-CHEST AP PORT-08405/2.00000...
                               ...                        
13255    A973206/02-21-1901-CHEST AP PORT-64271/2.00000...
13257    A973206/02-22-1901-CHEST AP PORT-48828/2.00000...
13259    A973206/02-25-1901-CHEST AP PORT-55663/4.00000...
13261    A973206/02-27-1901-CHEST AP VIEWONLY-10056/3.0...
13263    A973206/12-31-1900-CHEST AP VIEW ONLY-31522/2....
Name: filename, Length: 71, dtype: object
13120    A973206/01-01-1901-CHEST AP PORT CENTRAL LINE ...
13122    A973206/01-01-1901-CHEST AP PORT CENTRAL LINE ...
13124    A973206/01-02-1901-CHEST AP PORT-82807/2.00000...
13126    A973206/01-03-1901-CHEST AP PORT-48846/2.00000...
13128    A973206/01-04-1901-CHEST AP PORT-08405/2.00000...
              

13579    A993649/01-01-1901-CHEST AP PORT CENTRAL LINE ...
13581    A993649/01-01-1901-CHEST AP PORT-66037/2.00000...
13583    A993649/01-02-1901-CHEST AP PORT-40751/2.00000...
13585    A993649/01-04-1901-CHEST AP PORT CENTRAL LINE ...
13587    A993649/01-04-1901-CHEST AP VIEWONLY-17182/2.0...
13589    A993649/01-06-1901-CHEST AP VIEWONLY-49483/2.0...
13591    A993649/01-09-1901-CHEST AP VIEWONLY-52449/2.0...
13593    A993649/01-13-1901-CHEST AP PORT-83357/2.00000...
13597    A993649/01-20-1901-CHEST AP PORT-34320/5.00000...
13598    A993649/01-20-1901-CHEST AP PORT-34320/6.00000...
13599    A993649/01-20-1901-CHEST AP PORT-34320/7.00000...
13602    A993649/01-20-1901-CHEST AP PORT-66707/5.00000...
13603    A993649/01-20-1901-CHEST AP PORT-66707/6.00000...
13605    A993649/01-20-1901-CHEST AP PORT-92535/3.00000...
13607    A993649/01-21-1901-CHEST AP PORT-88080/2.00000...
13609    A993649/01-24-1901-CHEST AP PORT-41553/5.00000...
13611    A993649/12-26-1900-CHEST AP VIEWONLY-15212/2.0.

In [87]:
os.getcwd()

'C:\\Users\\Adonis McQueen\\Documents\\Flatiron\\Phase_5\\COVID19_MortalityPred'

In [86]:
os.listdir()

['.git',
 '.gitignore',
 '.ipynb_checkpoints',
 'Classes',
 'COVID19Models_notebook.ipynb',
 'COVID19_SBU',
 'COVID19_SBU_Dataprep.ipynb',
 'COVID19_xray_imganalysis.ipynb',
 'df.csv',
 'README.md']

In [23]:
source = '/c/Users/Adonis McQueen/Documents/Flatiron/Phase_5/COVID19_MortalityPred/COVID19_SBU/COVID-19-NY-SBU'
destination_dead = '/c/Users/Adonis McQueen/Documents/Flatiron/Phase_5/COVID19_MortalityPred/Classes/deceased'
destination_alive = 'C:\\Users\\Adonis McQueen\\Documents\\Flatiron\\Phase_5\\COVID19_MortalityPred\\Classes\\discharged'

In [24]:
sample = ['C:\\Users\\Adonis McQueen\\Documents\\Flatiron\\Phase_5\\COVID19_MortalityPred\\COVID19_SBU\\COVID-19-NY-SBU\\A000801\\01-03-1901-CHEST AP PORT-62879\\1.000000-AP-12195\\1-1.png']

In [90]:
# for file in sample:
#     shutil.move(file, destination_alive)

In [26]:
# #For full data move:
# -use the absolute file path
# -change all '/' to '\\'
# -add os.getcwd() + \\COVID19_SBU\\COVID-19-NY-SBU\\ + filename to get aboslute file path to move for source
# -destination path is fine for destination_alive, do the same for destination_dead

metadata['filename'] = metadata['filename'].str.replace("/", '\\\\')
    
metadata.head()

id patient_id  enhanced                          series  \
1  IMG00002    A000801      True  01-03-1901-CHEST AP PORT-62879   
3  IMG00004    A000801      True  01-03-1901-CHEST AP PORT-62879   
5  IMG00006    A000801      True  01-04-1901-CHEST AP PORT-17928   
7  IMG00008    A000801      True  01-04-1901-CHEST AP PORT-17928   
9  IMG00010    A000801      True  01-04-1901-CHEST AP PORT-38592   

                                            filename  
1  A000801\\01-03-1901-CHEST AP PORT-62879\\2.000...  
3  A000801\\01-03-1901-CHEST AP PORT-62879\\4.000...  
5  A000801\\01-04-1901-CHEST AP PORT-17928\\2.000...  
7  A000801\\01-04-1901-CHEST AP PORT-17928\\4.000...  
9  A000801\\01-04-1901-CHEST AP PORT-38592\\2.000...

In [29]:
#adding absolute file path to filenames for transfer: df['col'] = 'str' + df['col'].astype(str)

filestr = 'C:\\\\Users\\\\Adonis McQueen\\\\Documents\\\\Flatiron\\\\Phase_5\\\\COVID19_MortalityPred\\\\COVID19_SBU\\\\COVID-19-NY-SBU\\\\'

metadata['filename'] = filestr + metadata['filename'].astype(str)

metadata.head()

id patient_id  enhanced                          series  \
1  IMG00002    A000801      True  01-03-1901-CHEST AP PORT-62879   
3  IMG00004    A000801      True  01-03-1901-CHEST AP PORT-62879   
5  IMG00006    A000801      True  01-04-1901-CHEST AP PORT-17928   
7  IMG00008    A000801      True  01-04-1901-CHEST AP PORT-17928   
9  IMG00010    A000801      True  01-04-1901-CHEST AP PORT-38592   

                                            filename  
1  C:\\Users\\Adonis McQueen\\Documents\\Flatiron...  
3  C:\\Users\\Adonis McQueen\\Documents\\Flatiron...  
5  C:\\Users\\Adonis McQueen\\Documents\\Flatiron...  
7  C:\\Users\\Adonis McQueen\\Documents\\Flatiron...  
9  C:\\Users\\Adonis McQueen\\Documents\\Flatiron...

In [14]:
!pwd

/c/Users/Adonis McQueen/Documents/Flatiron/Phase_5/COVID19_MortalityPred


In [ ]:
# /c/Users/Adonis McQueen/Documents/Flatiron/Phase_5/COVID19_MortalityPred + /COVID19_SBU/COVID-19-NY-SBU/ + A000801/01-03-1901-CHEST AP PORT-62879/2.000000-AP-20460/1-1.png

In [ ]:
-see if patient is deceased
-then try to print filename
-create test dir
-move test file to target dir
-once successful, attempt full data move